# Concurso de Remoção da Prefeitura de São Paulo
__Fonte dos dados:__ <a href="http://diariooficial.imprensaoficial.com.br/nav_v4/index.asp?c=1">Imprensa Oficial: Caderno Suplementar DOC</a><br>
__Solicitante:__ SINDSEP - Secretaria de Educação <br>
__Problema:__ Transferir os dados do arquivo em PDF baixado do site Imprensa Oficial para o Excel com as seguintes colunas:

- Registro Funcional: Número de registro do funcionário
- Código Antigo: Antigo código de representação do cargo
- Código Novo: Novo código de representação do cargo
- Nome: Nome do servidor para remoção
- De (Código): Código de representação da unidade de origem
- De (Descrição): Unidade de origem
- Para (Código): Código de representação da unidade de destino
- Para (Descrição): Unidade de destino

# Código

## Bibliotecas

In [24]:
#Instalação de bibliotecas
!pip install pymupdf
#Importação de bibliotecas
import fitz as fz
import pandas as pd
import numpy as np

## Leitura do arquivo e gravação dos dados

In [25]:
with fz.open("Dados/remocao.pdf") as pdf:
    conteudo = ""
    for pagina in pdf:
        conteudo += pagina.get_text()
#conteudo

In [26]:
with open("Output.txt","w",encoding="utf-8") as text_file:
    text_file.write(conteudo)

## Manipulando os dados

In [27]:
#Localizando o início da tabela de dados
indice_dados = conteudo.find('REG.FUN.')
indice_dados

677

In [28]:
#Informação do cabeçalho do diário Oficial do Município (DOM)
#cabecalho_dom = pd.Series(texto[:indice_dados].split('\n'))
#cabecalho_dom
cabecalho_dom = np.array(conteudo[:indice_dados].replace('\n',' ').split('\n'))
cabecalho_dom

array(['Cidade de São Paulo Ricardo Nunes - Prefeito  Diário Oficial   Ano 66  São Paulo, quinta-feira, 18 de novembro de 2021  Número 220 CONCURSOS EDUCAÇÃO GABINETE DO SECRETÁRIO COMUNICADO Nº 1.288, DE 17 DE NOVEMBRO DE 2021. CONCURSOS DE REMOÇÃO – 2021 – RESULTADOS FINAIS DOS CONCURSOS O Secretário Municipal de Educação, no uso de suas atribuições legais e considerando o disposto no item 23 do Edital de Aber- tura de Inscrições e de Procedimentos dos Concursos de Remoção 2021, PUBLICA os resultados finais dos Concursos de Remoção  2021. Os resultados da remoção surtirão efeitos a partir de 01/01/2022. CONCURSO:001-REMOÇÃO PROF.TITULARES CARGO=3239-PROF.ED.INF.E ENS.FUND.I '],
      dtype='<U677')

In [49]:
#Dados para tratar
#dados = pd.Series(texto[indice_dados:].split('\n'))
#dados.head(10)
#dados = conteudo[indice_dados+22:].replace(' - ',' ')   #arrumar não haver traços
dados = conteudo[indice_dados+22:].replace(' - ',' ')   #arrumar não haver traços
dados = dados.replace(', \nPROFA.\n',' PROFA.\n ')        #arrumar \nPROFA.\n
dados = dados.replace(', \nPROFA\n',', PROFA\n')        #arrumar \nPROFA.\n, \nPROFA\n
dados = dados.replace(' 019214-CEU EMEI JARDIM VILA NOVA',' \n019214-CEU EMEI JARDIM VILA NOVA')        #arrumar \nPROFA.\n, \nPROFA\n
dados = dados.replace(', \nPROFA.\n',', PROFA.\n')        #arrumar , \nPROFA.\n
dados = dados.replace('JR. \nGONZAGUINHA\n','JR. GONZAGUINHA\n')        #arrumar JR. \nGONZAGUINHA\n
dados = dados.replace('KLEIN \nPUSSINELLI, PROFA.\n','KLEIN PUSSINELLI, PROFA.\n')        #arrumar JR. \nGONZAGUINHA\n
dados = dados.replace('GONCALVES, \nPROFESSORA NANY BENUTE\n','GONCALVES, PROFESSORA NANY BENUTE\n')        #arrumar GONCALVES, \nPROFESSORA- NANY BENUTE\n
#print(dados.find(', \nPROFA\n'))
#print(dados[840:880])
#dados = dados.replace(', \nPROFA\n',', PROFA\n')        #arrumar \nPROFA.\n, \nPROFA\n
#print(dados[840:880])
#print(dados.find(', \nPROFA\n'))
dados = np.array(dados.split('\n')) #arrumar \nPROFA.\n
dados


array(['5041236-06-7', 'ROSELI BELDA DALTON',
       '019199-EMEI CLEMENCIA FERREIRA DA SILVA', ...,
       'portal www.imprensaoficial.com.br',
       'quinta-feira, 18 de novembro de 2021 às 05:04:04', ''],
      dtype='<U126')

In [50]:
teste = dados.copy()
#t1 = teste[:500]
t1 = teste
t1

array(['5041236-06-7', 'ROSELI BELDA DALTON',
       '019199-EMEI CLEMENCIA FERREIRA DA SILVA', ...,
       'portal www.imprensaoficial.com.br',
       'quinta-feira, 18 de novembro de 2021 às 05:04:04', ''],
      dtype='<U126')

## Gerando o DF

In [51]:
linha = list()
erro = list()
dados_tabela = list()
col = 1
itr = 0
lin = 0
tst = False
reg = False
reg_fun = False
pesquisa = 0

for item in t1:
    item = item.strip()
    valida = True
    print(f'FOR Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
    if col == 1 and (item[:-3]).find('-') != -1 and 10<len(item)<13 and reg == False and len(linha) == 0:
        linha.append(item[:-3])
        pesquisa = (item[:-3]).find('-')
        print(f'1 Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}, find: {pesquisa}')
        col += 1
        valida = False
        reg = True
    elif col == 2 and reg == True and len(linha) == 1:
        linha.append(item)
        print(f'2 Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
        col += 1
        valida = False
    elif col == 3 and (item[:9]).find('-') != -1 and reg == True and len(linha) == 2:
        linha.append(item[:6])
        print(f'3 Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
        col += 1
        valida = False
    elif col == 4 and (item[:9]).find('-') != -1 and reg == True and len(linha) == 3:
        linha.append(item[:6])
        print(f'4 Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
        dados_tabela.append(linha)
        col = 1
        lin = lin + 1
        linha = list()
        reg = False
        valida = False
    elif col == 5:
        if tst == True:
            local = f't lin: {lin}, col: {col}, item: {item}, linha: '
            erro.append(local)
            print(f'### ERRRO: Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg_fun: {reg}, teste: {tst}, valida: {valida}')
            col = 1
            tst = False
            lin = lin + 1
            linha = list()
            valida = False
        else:
            print(f'### REINICIAR: Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
            col = 1
            tst += tst
    else:
        print(f'### VARRER: Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
        col += 1
        tst = True
print(f'### WHILE: Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')

FOR Lin: 0, Col: 1, item: 5041236-06-7, len: 12, reg: False, teste: False, valida: True
1 Lin: 0, Col: 1, item: 5041236-06-7, len: 12, reg: False, teste: False, valida: True, find: 7
FOR Lin: 0, Col: 2, item: ROSELI BELDA DALTON, len: 19, reg: True, teste: False, valida: True
2 Lin: 0, Col: 2, item: ROSELI BELDA DALTON, len: 19, reg: True, teste: False, valida: True
FOR Lin: 0, Col: 3, item: 019199-EMEI CLEMENCIA FERREIRA DA SILVA, len: 39, reg: True, teste: False, valida: True
3 Lin: 0, Col: 3, item: 019199-EMEI CLEMENCIA FERREIRA DA SILVA, len: 39, reg: True, teste: False, valida: True
FOR Lin: 0, Col: 4, item: 091138-EMEI ANTONIO LAPENNA, len: 27, reg: True, teste: False, valida: True
4 Lin: 0, Col: 4, item: 091138-EMEI ANTONIO LAPENNA, len: 27, reg: True, teste: False, valida: True
FOR Lin: 1, Col: 1, item: 5067324-05-6, len: 12, reg: False, teste: False, valida: True
1 Lin: 1, Col: 1, item: 5067324-05-6, len: 12, reg: False, teste: False, valida: True, find: 7
FOR Lin: 1, Col: 2, 

# Possíveis validações

## Com IF e find

In [ ]:
linha = list()
erro = list()
dados_tabela = list()
col = 1
itr = 0
lin = 0
tst = False
reg = False
reg_fun = False
pesquisa = 0

for item in t1:
    valida = True
    print(f'FOR Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
    if col == 1 and (item[:-3]).find('-') != -1 and 10<len(item)<13 and reg == False and len(linha) == 0:
        linha.append(item[:-3])
        pesquisa = (item[:-3]).find('-')
        print(f'1 Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}, find: {pesquisa}')
        col += 1
        valida = False
        reg = True
    elif col == 2 and reg == True and len(linha) == 1:
        linha.append(item)
        print(f'2 Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
        col += 1
        valida = False
    elif col == 3 and (item[:9]).find('-') != -1 and reg == True and len(linha) == 2:
        linha.append(item[:6])
        print(f'3 Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
        col += 1
        valida = False
    elif col == 4 and (item[:9]).find('-') != -1 and reg == True and len(linha) == 3:
        linha.append(item[:6])
        print(f'4 Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
        dados_tabela.append(linha)
        col = 1
        lin = lin + 1
        linha = list()
        reg = False
        valida = False
    elif col == 5:
        if tst == True:
            local = f't lin: {lin}, col: {col}, item: {item}, linha: '
            erro.append(local)
            print(f'### ERRRO: Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg_fun: {reg}, teste: {tst}, valida: {valida}')
            col = 1
            tst = False
            lin = lin + 1
            linha = list()
            valida = False
        else:
            print(f'### REINICIAR: Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
            col = 1
            tst += tst
    else:
        print(f'### VARRER: Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
        col += 1
        tst = True
print(f'### WHILE: Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')

## Com WHILE

In [ ]:
linha = list()
erro = list()
dados_tabela = list()
col = 0
itr = 0
lin = 0
tst = False
reg = False
reg_fun = False

for item in t1:
    valida = True
    print(f'FOR Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
    while valida:  
        if col == 1 and item.find('-') and 10<len(item)<13 and reg == False and len(linha) == 0:
            linha.append(item)
            print(f'1 Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
            col += 1
            valida = False
            reg = True
            break
        elif col == 2 and reg == True and len(linha) == 1:
            linha.append(item)
            print(f'2 Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
            col += 1
            valida = False
        elif col == 3 and (item[:9]).find('-') and reg == True and len(linha) == 2:
            linha.append(item[:6])
            print(f'3 Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
            col += 1
            valida = False
        elif col == 4 and (item[:9]).find('-') and reg == True and len(linha) == 3:
            linha.append(item[:6])
            print(f'4 Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
            dados_tabela.append(linha)
            col = 1
            lin = lin + 1
            linha = list()
            reg = False
            valida = False
        elif col == 5:
            if tst == True:
                local = f't lin: {lin}, col: {col}, item: {item}, linha: '
                erro.append(local)
                print(f'### ERRRO: Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg_fun: {reg}, teste: {tst}, valida: {valida}')
                col = 1
                tst = False
                lin = lin + 1
                linha = list()
                valida = False
            else:
                print(f'### REINICIAR: Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
                col = 1
                tst += tst
        else:
            print(f'### VARRER: Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
            col += 1
            tst = True
    print(f'### WHILE: Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')

## Com IF

In [ ]:
linha = list()
erro = list()
col = 1
lin = 0
dados_tabela = list()
for i in range(0,len(t1)):
    #if col <= 4:
    if col == 1 and len(t1[i]) == 12:
        linha.append(t1[i])
        print(f'Lin: {lin}, Col: {col}, item: {t1[i]}, len: {len(t1[i])}')
        col = col + 1
    elif col == 1 and len(t1[i]) != 12:
        #dados_tabela[lin-1] = dados_tabela[lin-1] + " " + t1[i]
        local = f'lin: {lin}, col: {col}, item: {t1[i]}'
        erro.append(local)
        print(f'erro: {t1[i]}')
        print(f'### Lin: {lin}, Col: {col}, item: {t1[i]}, len: {len(t1[i])}')    
    elif col == 3 and t1[i].find('-'):
        linha.append(t1[i][:6])
        print(f'Lin: {lin}, Col: {col}, item: {t1[i]}, len: {len(t1[i])}')
        col = col + 1
    elif col == 4 and t1[i].find('-'):
        linha.append(t1[i][:6])
        print(f'Lin: {lin}, Col: {col}, item: {t1[i]}, len: {len(t1[i])}')
        dados_tabela.append(linha)
        col = 1
        lin = lin + 1
        linha = list()
    else:
        linha.append(t1[i])
        print(f'Lin: {lin}, Col: {col}, item: {t1[i]}, len: {len(t1[i])}')
        col = col + 1

## While com find

In [74]:
linha = list()
erro = list()
dados_tabela = list()
col = 0
itr = 0
lin = 0
tst = False
reg = False
reg_fun = False

for item in t1:
    valida = True
    print(f'FOR Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
    while valida:  
        if col == 1 and item.find('-') != -1 and 10<len(item)<13 and reg == False and len(linha) == 0:
            linha.append(item)
            print(f'1 Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
            col += 1
            valida = False
            reg = True
            break
        elif col == 2 and reg == True and len(linha) == 1:
            linha.append(item)
            print(f'2 Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
            col += 1
            valida = False
        elif col == 3 and len(item)>=9 and reg == True and len(linha) == 2:
            if (item[:9]).find('-') != -1:
                linha.append(item[:6])
                print(f'3 Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
                col += 1
                valida = False
            else:
                col += 1
        elif col == 4 and len(item)>=9 and reg == True and len(linha) == 3:
            if (item[:9]).find('-') != -1:
                linha.append(item[:6])
                print(f'4 Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
                dados_tabela.append(linha)
                col = 1
                lin = lin + 1
                linha = list()
                reg = False
                valida = False
            else:
                col += 1
        elif col == 5:
            if tst == True:
                local = f't lin: {lin}, col: {col}, item: {item}, linha: '
                erro.append(local)
                print(f'### ERRRO: Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg_fun: {reg}, teste: {tst}, valida: {valida}')
                col = 1
                tst = False
                lin = lin + 1
                linha = list()
                valida = False
            else:
                print(f'### REINICIAR: Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
                col = 1
                tst += tst
        else:
            print(f'### VARRER: Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')
            col += 1
            tst = True
    print(f'### WHILE: Lin: {lin}, Col: {col}, item: {item}, len: {len(item)}, reg: {reg}, teste: {tst}, valida: {valida}')

FOR Lin: 0, Col: 0, item: 5041236-06-7, len: 12, reg: False, teste: False, valida: True
### VARRER: Lin: 0, Col: 0, item: 5041236-06-7, len: 12, reg: False, teste: False, valida: True
1 Lin: 0, Col: 1, item: 5041236-06-7, len: 12, reg: False, teste: True, valida: True
### WHILE: Lin: 0, Col: 2, item: 5041236-06-7, len: 12, reg: True, teste: True, valida: False
FOR Lin: 0, Col: 2, item: ROSELI BELDA DALTON, len: 19, reg: True, teste: True, valida: True
2 Lin: 0, Col: 2, item: ROSELI BELDA DALTON, len: 19, reg: True, teste: True, valida: True
### WHILE: Lin: 0, Col: 3, item: ROSELI BELDA DALTON, len: 19, reg: True, teste: True, valida: False
FOR Lin: 0, Col: 3, item: 019199-EMEI CLEMENCIA FERREIRA DA SILVA, len: 39, reg: True, teste: True, valida: True
3 Lin: 0, Col: 3, item: 019199-EMEI CLEMENCIA FERREIRA DA SILVA, len: 39, reg: True, teste: True, valida: True
### WHILE: Lin: 0, Col: 4, item: 019199-EMEI CLEMENCIA FERREIRA DA SILVA, len: 39, reg: True, teste: True, valida: False
FOR Lin

# Dataframe

In [52]:
df = pd.DataFrame(dados_tabela,columns=['REG.FUN.','NOME','DE','PARA'])
#df = pd.DataFrame(dados_tabela,columns=['REG.FUN.','DE','PARA'])
df
#df[40:80]
#df.head()

REG.FUN.                                   NOME      DE    PARA
0    5041236-0                    ROSELI BELDA DALTON  019199  091138
1    5067324-0       DORALICE FERNANDES DO NASCIMENTO  019365  090042
2    5096723-0                            ROZANA LIMA  091375  019234
3    5097126-0  SONIA REGINA DOS SANTOS RUIZ FABREGAT  013111  000221
4    5247829-0                   SANDRA BECKER CABBIA  093149  090433
..         ...                                    ...     ...     ...
115  6773591-0        MARCIA APARECIDA GOMES DE FARIA  090531  099244
116  6775144-0         ANALIA GONCALVES DE SOUZA LIMA  093424  090549
117  6776205-0             CLEIDE PEREIRA DE CARVALHO  019479  400875
118  6776221-0                      NEIDE HITOMI UEDA  093998  094056
119  6776345-0                RENATA BURRATTINO FELIX  019661  091448

[120 rows x 4 columns]

In [53]:
print(len(erro))
erro

6911


['t lin: 81, col: 5, item: 095541-EMEF OLIVAL COSTA, linha: ',
 't lin: 88, col: 5, item: CARLA BRAGA CARVALHO, linha: ',
 't lin: 89, col: 5, item: 090468-EMEI ZILDA DE FRANCESCHI, PROFA., linha: ',
 't lin: 90, col: 5, item: 095362-EMEF MAUA, BR. DE, linha: ',
 't lin: 114, col: 5, item: 093891-EMEF ARMANDO CRIDEY RIGHETTI, linha: ',
 't lin: 115, col: 5, item: 018279-EMEI CEZAR ROGERIO OLIVEIRA PERAMEZZA, PROF., linha: ',
 't lin: 126, col: 5, item: 019253-EMEI JOAO PAULO II, PAPA, linha: ',
 't lin: 127, col: 5, item: 6776884-02-3, linha: ',
 't lin: 128, col: 5, item: PATRICIA MARQUEZI, linha: ',
 't lin: 129, col: 5, item: DA SILVA, linha: ',
 't lin: 130, col: 5, item: 019612-CEMEI DOMINGOS DELGADO, linha: ',
 't lin: 131, col: 5, item: 019278-CEU EMEF VILA CURUCA, linha: ',
 't lin: 132, col: 5, item: 6784135-01-2, linha: ',
 't lin: 133, col: 5, item: ROSENEI MARIA ALVES FERREIRA SOBRAL, linha: ',
 't lin: 134, col: 5, item: 019357-CEU EMEI BRAZ JAIME ROMANO, linha: ',
 't lin

#Arrumar

In [ ]:
linha = list()
erro = list()
col = 1
lin = 0
dados_tabela = list()
for i in range(0,len(t1)):
    #if col <= 4:
    if col == 1 and len(t1[i]) == 12:
        linha.append(t1[i])
        print(f'Lin: {lin}, Col: {col}, item: {t1[i]}, len: {len(t1[i])}')
        col = col + 1
    elif col == 1 and len(t1[i]) != 12:
        #dados_tabela[lin-1] = dados_tabela[lin-1] + " " + t1[i]
        local = f'lin: {lin}, col: {col}, item: {t1[i]}'
        erro.append(local)
        print(f'erro: {t1[i]}')
        print(f'### Lin: {lin}, Col: {col}, item: {t1[i]}, len: {len(t1[i])}')
    elif col == 4:
        linha.append(t1[i])
        print(f'Lin: {lin}, Col: {col}, item: {t1[i]}, len: {len(t1[i])}')
        dados_tabela.append(linha)
        col = 1
        lin = lin + 1
        linha = list()
    else:
        linha.append(t1[i])
        print(f'Lin: {lin}, Col: {col}, item: {t1[i]}, len: {len(t1[i])}')
        col = col + 1
    #else:
    #    linha.append(t1[i])
    #    print(f'Col: {col}, item: {t1[i]}, len: {len(t1[i])}')
    #    dados_tabela.append(linha)
    #    col = 1
    #    linha = list()
    #linha.append(t1[i])
    #print(f'Col: {col}, item: {t1[i]}, len: {len(t1[i])}')
#dados_tabela

In [ ]:
linha = list()
col = 0
dados_tabela = list()
for i in range(0,len(dados)):
    if col < 4:
        col = col + 1
    else:
        dados_tabela.append(linha)
        col = 1
        linha = list()
    linha.append(dados[i])

In [ ]:
linha = list()
col = 0
lin = 0
dados_tabela = list()
for i in range(0,len(dados)):
    if col < 4:
        if col == 0 & len(dados[i]) != 12:
            dados_tabela[lin-1] = dados_tabela[lin-1] + ' ' + dados[i]
            col = 0
        else:
            col = col + 1
            linha.append(dados[i])
    else:
        dados_tabela.append(linha)
        lin = lin + 1
        col = 1
        linha = list()
#dados_tabela

In [ ]:
len(dados[1897])

In [ ]:
df.drop([0])

In [ ]:
df.values